In [94]:
# ! pip install scikit-learn 
# ! pip install numpy
# ! pip install pandas
# ! pip install xgboost
# ! pip install graphviz
# ! pip install matplotlib
! brew update
! brew install graphviz

Already up-to-date.
==> Downloading https://ghcr.io/v2/homebrew/core/graphviz/manifests/9.0.0
Already downloaded: /Users/walker/Library/Caches/Homebrew/downloads/5b5226cdddfdb22a670a03a24017bdadd4a3bda68021a92ce6b32e06bc9f28a2--graphviz-9.0.0.bottle_manifest.json
==> Fetching dependencies for graphviz: harfbuzz, pango, librsvg and libtool
==> Downloading https://ghcr.io/v2/homebrew/core/harfbuzz/manifests/8.3.0
Already downloaded: /Users/walker/Library/Caches/Homebrew/downloads/8fccd91a473694ef9d916ce061ae69cb18243bdab491757fae06fed911dd5b63--harfbuzz-8.3.0.bottle_manifest.json
==> Fetching dependencies for harfbuzz: cairo
==> Downloading https://ghcr.io/v2/homebrew/core/cairo/manifests/1.18.0
Already downloaded: /Users/walker/Library/Caches/Homebrew/downloads/1b8b7f19e38cb0e029497dfe0ad3f3557f605025c5575bdfe86c17b889c6e6d1--cairo-1.18.0.bottle_manifest.json
==> Fetching cairo
==> Downloading https://ghcr.io/v2/homebrew/core/cairo/blobs/sha256:18232de7a188
Already downloaded: /Users/wa

In [95]:
import os
import pandas as pd
import numpy as np
import csv
import math

from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import scale
from sklearn import set_config 

from xgboost import XGBRegressor

from graphviz import Digraph
from xgboost import plot_tree
import matplotlib.pyplot as plt

In [149]:
def preprocessData(singleData):
    singleData[5] -= 24.5
    singleData[6] -= 121
    if singleData[3] == 0:
        singleData[3] = 24
    if singleData[4] == 0:
        singleData[4] = 60
    singleData[4] /= 60
    # singleData[7] = min(singleData[7], singleData[8])
    # singleData.pop(8)
    
    return singleData

def readDataset(data_filepath, inference_filepath):
    assert os.path.exists(data_filepath)
    filenames = os.listdir(data_filepath)
    if '.DS_Store' in filenames:
        filenames.remove('.DS_Store')
    filenames = sorted(filenames)
    dataset = []
    for idx, filename in enumerate(filenames):
        data = (pd.read_csv(data_filepath + filename).values).tolist()
        for single_data in data:
            single_data = preprocessData(single_data)
            dataset.append(single_data)

    testDataset = []
    assert os.path.exists(inference_filepath)
    filenames = os.listdir(inference_filepath)
    if '.DS_Store' in filenames:
        filenames.remove('.DS_Store')
    filenames = sorted(filenames, reverse=True)
    testset = []
    for idx, filename in enumerate(filenames):
        if filename == "inf_1211_to_1217.csv":
            continue
        print(filename)
        data = (pd.read_csv(inference_filepath + filename).values).tolist()
        for single_data in data:
            single_data = preprocessData(single_data)
            testset.append(single_data)
    return dataset, testset

In [153]:
config = {
    "data_filepath": 'dataset_w_csv/',
    # "data_filepath": '/kaggle/input/dataset-1201-new/dataset_w_csv/',
    "inference_filepath": 'inference_w_csv/',
    # "inference_filepath": '/kaggle/input/inference-1204/inference_csv/',
    # "inference_filepath": '/kaggle/input/inference-new-1204/inference_w_csv/',
    "outputFilename": "results/prediction_GBDT.csv"
}

In [154]:
def splitFeaturesLabels(dataset, type):
    # month, day, weekday, hr, min, lat, lng, dist, act, ratio, sbi, tot, title, act_title
    if type == "train":
        features = np.array(dataset[:,:8], dtype=float)
        labels = np.array(dataset[:,8], dtype=float)
        return features, labels
    elif type == "test":
        features = np.array(dataset[:,:8], dtype=float)
        titles = []
        tots = []
        for single_data in dataset:
            tots.append(int(single_data[8]))
            titles.append(single_data[9])
        return features, titles, tots
    else:
        raise NotImplementedError

In [155]:
dataset, testset = readDataset(config['data_filepath'], config['inference_filepath'])
xtrain, ytrain = splitFeaturesLabels(np.array(dataset), "train")
xtest, titles, tots = splitFeaturesLabels(np.array(testset), "test")

print(xtest[0])
print(tots[0])
# xtrain = scale(xtrain)
# xtest = scale(xtest)

inf_1204_to_1210.csv
inf_1021_to_1024.csv
[12.       4.       1.      24.       1.       0.52605  0.5436   1.     ]
28


In [156]:
print(len(xtrain))
print(len(ytrain))
print(len(xtest))
print(len(titles))
print(len(tots))

459984
459984
88704
88704
88704


In [161]:
GBDT = XGBRegressor(n_estimators=1000, verbosity=1, n_jobs=-1, max_depth=6)
print(GBDT)

XGBRegressor(base_score=None, booster=None, callbacks=None,
             colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=None, device=None, early_stopping_rounds=None,
             enable_categorical=False, eval_metric=None, feature_types=None,
             gamma=None, grow_policy=None, importance_type=None,
             interaction_constraints=None, learning_rate=None, max_bin=None,
             max_cat_threshold=None, max_cat_to_onehot=None,
             max_delta_step=None, max_depth=6, max_leaves=None,
             min_child_weight=None, missing=nan, monotone_constraints=None,
             multi_strategy=None, n_estimators=1000, n_jobs=-1,
             num_parallel_tree=None, random_state=None, ...)


In [162]:
GBDT.fit(xtrain, ytrain)

score = GBDT.score(xtrain, ytrain)
print("R-squared:", score) 
 

R-squared: 0.7523073322679749


In [163]:
ypreds = GBDT.predict(xtest)
for i in range(len(ypreds)):
    if ypreds[i] < 0:
        ypreds[i] = 0

assert len(ypreds) == len(titles) == len(tots)
prediction = [['id','sbi']]
for (pred, tot, title) in zip(ypreds, tots, titles):
    prediction.append([title, pred*tot])

with open(config['outputFilename'], 'w', newline='') as file:
# Step 4: Using csv.writer to write the list to the CSV file
    writer = csv.writer(file)
    writer.writerows(prediction) # Use writerows for nested list
    
print("output file written")
        
# mse = mean_squared_error(ytest, ypred)
# print("MSE: ", mse)
# print("RMSE: ", mse*(1/2.0)) 

output file written


In [164]:
plot_tree(GBDT)
fig = plt.gcf()
fig.set_size_inches(300, 300)
plt.show()

python(52564) MallocStackLogging: can't turn off malloc stack logging because it was not enabled.
